# Exercice 2 - System evaluation

## Imports

In [37]:
import pandas as pd
import numpy as np

## Load data

Define the path of the data file

In [38]:
path = "ex2-system-a.csv"

Read the CSV file using `read_csv`

In [39]:
dataset_a = pd.read_csv(path, sep=";", index_col=False, names=["0", "1", "2", "3", "4", "5", "6", "7", "8", "9", "y_true"])

Display first rows

In [40]:
dataset_a.head()

0             1             2             3             4  \
0  5.348450e-08  7.493480e-10  8.083470e-07  2.082290e-05  5.222360e-10   
1  1.334270e-03  3.202960e-05  8.504280e-01  1.669090e-03  1.546460e-07   
2  3.643050e-06  9.962760e-01  2.045910e-03  4.210530e-04  2.194020e-05   
3  9.998200e-01  2.550390e-10  1.112010e-05  1.653200e-05  5.375730e-10   
4  2.092460e-08  7.464220e-08  3.560820e-05  5.496200e-07  9.988960e-01   

              5             6             7             8         9  y_true  
0  2.330260e-08  5.241270e-12  9.999650e-01  4.808590e-07  0.000013       7  
1  2.412940e-04  1.448280e-01  1.122810e-11  1.456330e-03  0.000011       2  
2  1.644130e-05  2.838160e-04  3.722960e-04  5.150120e-04  0.000044       1  
3  8.999750e-05  9.380920e-06  4.464470e-05  2.418440e-06  0.000006       0  
4  3.070920e-08  2.346150e-04  9.748010e-07  1.071610e-06  0.000831       4

Store some useful statistics (class names + number of classes)

In [41]:
class_names = ["0", "1", "2", "3", "4", "5", "6", "7", "8", "9"]
nb_classes = len(class_names)

## Exercise's steps

a) Write a function to take classification decisions on such outputs according to Bayes’rule.

In [42]:
def bayes_classification(df):
        """
        Take classification decisions according to Bayes rule.

        Parameters
        ----------
        df : Pandas DataFrame of shape (n_samples, n_features + ground truth)
        Dataset.

        Returns
        -------
        preds : Numpy array of shape (n_samples,)
        Class labels for each data sample.
        """
        y_pred = []
        for i in range(df.shape[0]):
                index = np.argmax(df.iloc[i,:10]) # take all the line except the y value
                y_pred.append(index)
                
        return y_pred


b) What is the overall error rate of the system ?

In [43]:
# Your code here: compute and print the error rate of the system
y_pred_a = bayes_classification(dataset_a)

correct = 0
for i in range(0, len(y_pred_a)):
    if(dataset_a.iloc[i,10] == y_pred_a[i]):
        correct += 1

success = correct/len(y_pred_a)
print(f"Error rate = {1-success}")

Error rate = 0.10729999999999995


c) Compute and report the confusion matrix of the system.

In [44]:
def confusion_matrix(y_true, y_pred, n_classes):
    """
    Compute the confusion matrix.
        
    Parameters
    ----------
    y_true : Numpy array of shape (n_samples,)
             Ground truth.
    y_pred : Numpy array of shape (n_samples,)
             Predictions.
    n_classes : Integer
                Number of classes.
         
    Returns
    -------
    cm : Numpy array of shape (n_classes, n_classes)
         Confusion matrix.
    """
    matrix = np.zeros((n_classes, n_classes))

    for i in range(0, len(y_pred)):
        matrix[y_true[i], y_pred[i]] += 1 

    return matrix

In [45]:
# Your code here: compute and print the confusion matrix

cm_a = confusion_matrix(dataset_a.iloc[:,10], y_pred_a, nb_classes)

#headers
print("     ", end="")
for j in range(nb_classes):
    print(f"{j:5d}", end="")
print()

#rows
for i in range(nb_classes):
    match i:
        case 3:
            print("t", end="")
        case 4:
            print("r", end="")
        case 5:
            print("u", end="")
        case 6:
            print("e", end="")
        case _:
            print(" ", end="")

    print(f"{i:3d} |", end="")
    for j in range(nb_classes):
        print(f"{int(cm_a[i, j]):5d}", end="")

    print()


print("                     predicted          ")
# print(cm.astype(int))

         0    1    2    3    4    5    6    7    8    9
   0 |  944    0   11    0    0    2   10    7    5    1
   1 |    0 1112    2    3    1    4    3    1    9    0
   2 |   10    6  921   12   15    3   19   15   26    5
t  3 |    1    1   31  862    2   72    5   14   12   10
r  4 |    2    3    6    2  910    1   12    6    4   36
u  5 |   12    3    6   29   19  768   19    9   21    6
e  6 |   14    3   21    2   22   28  865    0    3    0
   7 |    0   14   30    9    7    2    1  929    3   33
   8 |   12   16   18   26   24   46   22   19  772   19
   9 |   10    4    6   22   53   18    0   48    4  844
                     predicted          


d) What are the worst and best classes in terms of precision and recall ?

In [46]:
def precision_per_class(cm):
    """
    Compute the precision per class.
        
    Parameters
    ----------
    cm : Numpy array of shape (n_classes, n_classes)
         Confusion matrix.
         
    Returns
    -------
    precisions : Numpy array of shape (n_classes,)
                 Precision per class.
    """
    rates = []
    for i in range(cm.shape[1]):
          correct = cm[i,i]
          incorrect = 0
          for j in range(cm.shape[0]):
               if i != j:
                    incorrect += cm[j,i]

          rates.append(correct/(correct+incorrect))

    return rates
               
               

In [47]:
def recall_per_class(cm):
    """
    Compute the recall per class.
        
    Parameters
    ----------
    cm : Numpy array of shape (n_classes, n_classes)
         Confusion matrix.
         
    Returns
    -------
    recalls : Numpy array of shape (n_classes,)
              Recall per class.
    """
    rates = []
    for i in range(cm.shape[0]):
          correct = cm[i,i]
          incorrect = 0
          for j in range(cm.shape[1]):
               if i != j:
                    incorrect += cm[i,j]

          rates.append(correct/(correct+incorrect))

    return rates

In [48]:
# Your code here: find and print the worst and best classes in terms of precision
precision_a = precision_per_class(cm_a)

for i in range(len(precision_a)):
    print(f"Class {i}, precision = {precision_a[i]}")

print("")

print(f"Best = class {np.argmax(precision_a)}, {precision_a[np.argmax(precision_a)]}")
print(f"Worst = class {np.argmin(precision_a)}, {precision_a[np.argmin(precision_a)]}")


Class 0, precision = 0.9393034825870646
Class 1, precision = 0.9569707401032702
Class 2, precision = 0.8754752851711026
Class 3, precision = 0.8914167528438469
Class 4, precision = 0.8641975308641975
Class 5, precision = 0.8135593220338984
Class 6, precision = 0.9048117154811716
Class 7, precision = 0.8864503816793893
Class 8, precision = 0.8987194412107101
Class 9, precision = 0.8846960167714885

Best = class 1, 0.9569707401032702
Worst = class 5, 0.8135593220338984


In [49]:
# Your code here: find and print the worst and best classes in terms of recall

recall_a = recall_per_class(cm_a)

for i in range(len(recall_a)):
    print(f"Class {i}, recall = {recall_a[i]}")

print("")

print(f"Best = class {np.argmax(recall_a)}, {recall_a[np.argmax(recall_a)]}")
print(f"Worst = class {np.argmin(recall_a)}, {recall_a[np.argmin(recall_a)]}")


Class 0, recall = 0.963265306122449
Class 1, recall = 0.9797356828193833
Class 2, recall = 0.8924418604651163
Class 3, recall = 0.8534653465346534
Class 4, recall = 0.9266802443991853
Class 5, recall = 0.8609865470852018
Class 6, recall = 0.9029227557411273
Class 7, recall = 0.9036964980544747
Class 8, recall = 0.7926078028747433
Class 9, recall = 0.8364717542120912

Best = class 1, 0.9797356828193833
Worst = class 8, 0.7926078028747433


e) In file `ex1-system-b.csv` you find the output of a second system B. What is the best system between (a) and (b) in terms of error rate and F1.

In [50]:
# Your code here: load the data of the system B
path = "ex2-system-b.csv"
dataset_b = pd.read_csv(path, sep=";", index_col=False, names=["0", "1", "2", "3", "4", "5", "6", "7", "8", "9", "y_true"])


In [51]:
def system_accuracy(cm):
    """
    Compute the system accuracy.
        
    Parameters
    ----------
    cm : Numpy array of shape (n_classes, n_classes)
         Confusion matrix.
         
    Returns
    -------
    accuracy : Float
               Accuracy of the system.
    """

    diag = 0
    for i in range(cm.shape[0]):
          diag += cm[i,i]

    acc = diag / np.sum(cm)
    return acc

In [52]:
def system_f1_score(cm):
    """
    Compute the system F1 score.
        
    Parameters
    ----------
    cm : Numpy array of shape (n_classes, n_classes)
         Confusion matrix.
         
    Returns
    -------
    f1_score : Float
               F1 score of the system.
    """

    f1 = []
    precision = precision_per_class(cm)
    recall = recall_per_class(cm)

    for i in range(0, len(precision)):
     f1.append(2*((precision[i] * recall[i])/(precision[i] + recall[i])))
    return np.sum(f1)/len(f1)


In [53]:
# Your code here: compute and print the accuracy and the F1 score of the system A

acc_a = system_accuracy(cm_a)
print(f"System A accuracy = {acc_a}")

f1_a = system_f1_score(cm_a)

print(f"System A f1 = {f1_a}")

System A accuracy = 0.8927
System A f1 = 0.8907308492877297


In [54]:
# Your code here: compute and print the accuracy and the F1 score of the system B
y_pred_b = bayes_classification(dataset_b)
cm_b = confusion_matrix(dataset_b.iloc[:,10], y_pred_b, nb_classes)

acc_b = system_accuracy(cm_b)
print(f"System A accuracy = {acc_b}")

f1_b = system_f1_score(cm_b)

print(f"System A f1 = {f1_b}")

System A accuracy = 0.9613
System A f1 = 0.9608568150389065
